## EE 372 Assignment 3

#### Name:  
#### Date: 

In [ ]:
%matplotlib inline

# The only libraries you should need for this assignment. 
# Execute this cell first. (You should get a sine wave.)
import matplotlib.pyplot as plt
import numpy as np

x = np.arange(0,1.0, 0.01)
y = np.sin(2*np.pi*x)
plt.plot(x,y)
plt.grid()
plt.xlabel('x')
plt.ylabel('y')
plt.title('Example plot')

### Question I: Minhashing

1.

We can describe a read as a set of unique overlapping $k$-mers, and we would expect similar reads to have similar sets. Write a function that takes $k$ and a read as inputs and outputs a dictionary indicating which of the $4^k$ $k$-mers are in the read.

3.

Write a function to compute the Jaccard similarity between two dictionaries outputted by your function from part 1. Using this function and the one you wrote for part 1, compute the Jaccard similarity between the reads <tt>CATGGACCGACCAG</tt> and <tt>GCAGTACCGATCGT</tt> for $k = 3$. What is the runtime complexity of your function? If you have $N$ reads of length $L$ each, what is the worst-case runtime complexity for computing the Jaccard similarity between every pair of reads?

### Question II: Haplotype phasing

1.

How many measurements are in the matrix?

2.

Is the graph connected?

3.

What is the maximum number of measurements between two SNPs?

5.

Download the ground truth of SNPs from [here](http://data-science-sequencing.github.io/Win2018/assets/assignment3/ground_truth.pkl). Get the primary eigenvector of the window of the first 200 SNPs in the adjacency matrix and find its correlation coefficient with the ground truth. Repeat with the full 5000-by-5000 adjacency matrix. How does the correlation coefficient change? Why?

### Question III: RNA-seq Quantification

1.

Implement the EM algorithm for the error-free case where all transcripts have the same length. Fill in the code in the last cell of the ipython notebook.

In [ ]:
# This code was adapted from a lab designed for UC Berkeley's EE126 course

from __future__ import division
import numpy as np
t = ['ATCTCGACGCACTGC', 'GAGTTCGAACTCTTC', 'AGAGTTCCAGTGTCA',
     'AAAGCTCACTGCGGA', 'AGCGATATCAGAGTD']
K = len(t) # Number of transcripts

rho = np.random.rand(K)
rho /= sum(rho)
print rho
# This rho is unknown to us

In [ ]:
# sample pmf according to rho
def rand_choice( pmf ): 
    v = np.random.rand()
    tmp = 0
    for i in range(len(pmf)):
        each_val = pmf[i]
        tmp += each_val
        if v <= tmp:
            return i

# randomly generate a read from a randomly chosen transcript
def random_read( t, rho, L ): 
    chosen_seq = t[rand_choice( rho )]
    start_idx = np.random.randint(0,len(chosen_seq) - L )
    end_idx = start_idx + L
    return chosen_seq[ start_idx:end_idx ]
        
N = 1000 # Number of reads
L = 5    # Length of each read

reads = []
for i in range(N):
    reads.append( random_read(t, rho, L) )
    
print 'First 20 reads...\n', reads[0:20]   

In [ ]:
N_iter = 100 # number of E/M iterations

# Naive alignment algorithm for no-error situation
def find_all_alignments(t, read):
    tmp = []
    for j in range(len(t)):
        if read in t[j]:
            tmp.append(j)
    return tmp

# A: Compatibility List. A[i] is a list of transcripts that read i aligns to
A = []
for each_read in reads:
    A.append( find_all_alignments(t, each_read) )

Z = np.zeros([N, K]) # hidden state prior
rho_est = (1/K)*np.ones([1,K])

# ==============================================================================
# Your EM code here. Save your final answer as rho_est

# First initialize Z
        
# EM iterations
for iter in range(N_iter):
    # E step
    rho_est =1
    # M step
    
# ==============================================================================
    
print '(real) rho', rho
print '(est.) rho', rho_est

### Question IV: Single-cell RNA-seq

In [ ]:
# Load data
X = np.loadtxt('Zeisel_data/Zeisel_expr.txt').T
genes = np.loadtxt('Zeisel_data/Zeisel_genes.txt', delimiter='\n', dtype=str)
labels = np.loadtxt('Zeisel_data/Zeisel_labels.txt', delimiter='\n', dtype=str)

2.

Plot two histograms: log(total counts) across cells and log(total counts) across genes. Why do we need to take a log here? What does this say about the data? Remove the columns of the matrix corresponding to genes that are expressed less than 25 times across all cells. How many genes are removed?

3.

Transform the data by adding 1 to all entries and taking the log (this is common practice). Two common dimensionality reduction strategies are principal component analysis (PCA) and t-distributed stochastic neighbor embedding (tSNE). You can implement PCA using the Python [sklearn package](http://scikit-learn.org/stable/modules/generated/sklearn.decomposition.PCA.html). We recommend [this](https://github.com/danielfrg/tsne) tSNE package for generating a tSNE embedding. List a pro and a con of each of the two methods. Create the following three plots and report what you see (for all plots, color points by their label):
- Run PCA and plot the first two principal components
- Run tSNE and plot the first two tSNE components (Note: this may take a few minutes)
- Run tSNE on the top 50 principal components and plot the first two tSNE components

4.

Using sklearn, we will test 4 different [clustering algorithms]((http://scikit-learn.org/stable/modules/clustering.html) on the dataset and evaluate their performance using the true labels provided by the authors. The four clustering methods are K-means clustering, spectral clustering, affinity propagation, and density-based spatial clustering of applications with noise (DBSCAN). Using the top 50 principal components for the log-transformed data, for each clustering method:
- Describe the hyperparameters one needs to tune
- Tune the hyperparameters until you obtain reasonable labels (i.e. you obtain about 9 clusters)
- Report your final hyperparameters
- Compare your labels to the true labels using sklearn's [adjusted Rand Index](http://scikit-learn.org/stable/modules/generated/sklearn.metrics.adjusted_rand_score.html).

5.

Using scipy's [_t_-test](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.ttest_ind.html) function and the log-transformed data, identify the top 5 most significant genes for each of the authors' reported clusters.